In [8]:
# REFERENSI
# https://www.youtube.com/watch?v=b06pFMIRO0I

In [9]:
import warnings
warnings.filterwarnings('ignore')

In [10]:
import pandas as pd
import plotly.graph_objects as go
from scipy import fftpack
import numpy as np

# Linear Accelerometer

In [11]:
df_accelerometer = pd.read_excel('https://github.com/krobus00/IoT-Milestone-1/blob/master/dataset/l%202022-05-29%2015-04-22.xls?raw=true')
# rename column agar mudah diakses
df_accelerometer.rename(columns={
    'Linear Acceleration x (m/s^2)' :'Ax',
    'Linear Acceleration y (m/s^2)':'Ay',
    'Linear Acceleration z (m/s^2)':'Az',
    }, inplace=True)
# slice dataset karena perekaman dilakukan selama 500 detik
df_accelerometer = df_accelerometer[df_accelerometer['Time (s)'] <= 300]
# membuat kolom time menjadi index agar dapat digunakan dalam plot timeseries
df_accelerometer.set_index('Time (s)', inplace=True)

In [12]:
df_accelerometer.sample(5)

Ax        Ay        Az
Time (s)                                
257.854600 -0.008668 -0.009436 -0.004106
192.303145 -0.000621  0.003501  0.003426
231.717780 -0.003563  0.003050 -0.002231
213.779547 -0.000938 -0.000899  0.000898
1.279414   -0.008871  0.001576  0.006685

In [13]:
df_accelerometer_dominan = df_accelerometer[['Az']]

In [14]:
n = len(df_accelerometer_dominan)
df_accelerometer_dominan['Az'] = df_accelerometer_dominan['Az'] - (sum(df_accelerometer_dominan['Az'])/n)

In [15]:
df_accelerometer_dominan.sample(5)

Az
Time (s)            
148.855821 -0.004714
156.027297 -0.001848
173.261604  0.001854
181.289083 -0.000788
269.610549 -0.001408

In [16]:
# trace1 digunakan untuk menampilkan plot dari sumbu dominan
trace1 = go.Scatter(
    x = df_accelerometer_dominan.index,
    y = df_accelerometer_dominan['Az'].values,
    mode = 'lines',
    name = 'Ax'
)

layout = go.Layout(
    title = "Plot Timeseries ",
    xaxis = {'title' : "Time (s)"},
    yaxis = {'title' : "m/s^2"}
)
fig = go.Figure(data=[trace1], layout=layout)
fig.show()

In [17]:
time_step = 0.02
time_vec = df_accelerometer_dominan.index
sig = df_accelerometer_dominan['Az'].values

In [18]:
sig_fft = fftpack.fft(sig)
amplitude = np.abs(sig_fft)

In [19]:
sample_freq = fftpack.fftfreq(sig.size, d=time_step)
amp_freq = np.array([amplitude,sample_freq])
amp_position = amp_freq[0,:].argmax()
peak_freq = amp_freq[1,amp_position]

In [20]:
high_freq_fft = sig_fft.copy()
high_freq_fft[np.abs(sample_freq) > peak_freq] = 0
filterred_sig = np.real(fftpack.ifft(high_freq_fft))

In [21]:
# trace1 digunakan untuk menampilkan plot dari fft
trace1 = go.Scatter(
    x = time_vec,
    y = filterred_sig,
    mode = 'lines',
    name = 'Ax'
)

layout = go.Layout(
    title = "Plot Timeseries (Frequency Domain)",
    xaxis = {'title' : "Time (s)"},
    yaxis = {'title' : "Amplitude"}
)
fig = go.Figure(data=[trace1], layout=layout)
fig.show()

In [22]:
df_mark_accelerometer = pd.read_excel('https://github.com/krobus00/IoT-Milestone-1/blob/master/dataset/manual_accelerometer.xlsx?raw=true')
# rename column agar mudah diakses
df_mark_accelerometer.rename(columns={
    'Jenis Kendaraan' :'type',
    'Kendaraan':'vehicle',
    }, inplace=True)
# membuat kolom time menjadi index agar dapat digunakan dalam plot timeseries
df_mark_accelerometer.set_index('Time (s)', inplace=True)


x = {'Ringan': 0, "Sedang": 1, "Berat": 2}
df_mark_accelerometer['type'] = df_mark_accelerometer['type'].map(x)
df_ringan = df_mark_accelerometer[df_mark_accelerometer['type'] == 0]
df_sedang = df_mark_accelerometer[df_mark_accelerometer['type'] == 1]
x = {1: 0}
df_sedang['type'] = df_sedang['type'].map(x)
df_berat = df_mark_accelerometer[df_mark_accelerometer['type'] == 2]
x = {2: 0}
df_berat['type'] = df_berat['type'].map(x)

In [23]:
# trace1 digunakan untuk menampilkan plot dari fft
trace1 = go.Scatter(
    x=time_vec,
    y=filterred_sig,
    mode='lines',
    name='Ax'
)

trace_ringan = go.Scatter(
    mode='markers',
    x=df_ringan.index,
    y=df_ringan['type'].values,
    name='Ringan',
    marker=dict(
        color='lightBlue',
        size=10,
        line=dict(
            color='black',
            width=2
        )
    ),
)
trace_sedang = go.Scatter(
    mode='markers',
    x=df_sedang.index,
    y=df_sedang['type'].values,
    name='Sedang',
    marker=dict(
        color='orange',
        size=10,
        line=dict(
            color='black',
            width=2
        )
    ),
)
trace_berat = go.Scatter(
    mode='markers',
    x=df_berat.index,
    y=df_berat['type'].values,
    name='Berat',
    marker=dict(
        color='yellow',
        size=10,
        line=dict(
            color='black',
            width=2
        )
    ),
)
layout = go.Layout(
    title="Plot Timeseries ",
    xaxis={'title': "Time (s)"},
    yaxis={'title': "Amplitude"}
)
fig = go.Figure(data=[trace1, trace_ringan, trace_sedang,
                trace_berat], layout=layout)
fig.show()


# Audioscope

In [24]:
df_audio = pd.read_excel('https://github.com/krobus00/IoT-Milestone-1/blob/master/dataset/a%202022-06-08%2009-31-16.xls?raw=true')
# rename column agar mudah diakses
df_audio.rename(columns={
    'Amplitude (a.u.)' :'Amplitude',
    }, inplace=True)
# slice dataset karena perekaman dilakukan selama 500 detik
df_audio = df_audio[df_audio['Time (ms)'] <= 300]
# membuat kolom time menjadi index agar dapat digunakan dalam plot timeseries
df_audio.set_index('Time (ms)', inplace=True)

In [25]:
n = len(df_audio)
df_audio['Amplitude'] = df_audio['Amplitude'] - (sum(df_audio['Amplitude'])/n)

In [26]:
df_audio.sample(5)

Amplitude
Time (ms)            
67.523391    0.007969
229.237850  -0.005855
147.193075  -0.007656
80.898898   -0.012753
266.864275   0.003148

In [27]:
# trace1 digunakan untuk menampilkan plot dari sumbu dominan
trace1 = go.Scatter(
    x = df_audio.index,
    y = df_audio['Amplitude'].values,
    mode = 'lines',
    name = 'Ax'
)

layout = go.Layout(
    title = "Plot Timeseries ",
    xaxis = {'title' : "Time (ms)"},
    yaxis = {'title' : "a. u"}
)
fig = go.Figure(data=[trace1], layout=layout)
fig.show()

In [28]:
time_step = 0.02
time_vec = df_audio.index
sig = df_audio['Amplitude'].values

In [29]:
sig_fft = fftpack.fft(sig)
amplitude = np.abs(sig_fft)

In [30]:
sample_freq = fftpack.fftfreq(sig.size, d=time_step)
amp_freq = np.array([amplitude,sample_freq])
amp_position = amp_freq[0,:].argmax()
peak_freq = amp_freq[1,amp_position]

In [31]:
high_freq_fft = sig_fft.copy()
high_freq_fft[np.abs(sample_freq) > peak_freq] = 0
filterred_sig = np.real(fftpack.ifft(high_freq_fft))

In [32]:
# trace1 digunakan untuk menampilkan plot dari fft
trace1 = go.Scatter(
    x = time_vec,
    y = filterred_sig,
    mode = 'lines',
    name = 'Ax'
)

layout = go.Layout(
    title = "Plot Timeseries (Frequency Domain)",
    xaxis = {'title' : "Time (ms)"},
    yaxis = {'title' : "Amplitude"}
)
fig = go.Figure(data=[trace1], layout=layout)
fig.show()

In [33]:
df_mark_audio = pd.read_excel('https://github.com/krobus00/IoT-Milestone-1/blob/master/dataset/manual_audio.xlsx?raw=true')
# rename column agar mudah diakses
df_mark_audio.rename(columns={
    'Jenis Kendaraan' :'type',
    'Kendaraan':'vehicle',
    }, inplace=True)
# membuat kolom time menjadi index agar dapat digunakan dalam plot timeseries
df_mark_audio.set_index('Time (ms)', inplace=True)


x = {'Ringan': 0, "Sedang": 1, "Berat": 2}
df_mark_audio['type'] = df_mark_audio['type'].map(x)
df_ringan = df_mark_audio[df_mark_audio['type'] == 0]
df_sedang = df_mark_audio[df_mark_audio['type'] == 1]
x = {1: 0}
df_sedang['type'] = df_sedang['type'].map(x)
df_berat = df_mark_audio[df_mark_audio['type'] == 2]
x = {2: 0}
df_berat['type'] = df_berat['type'].map(x)

In [34]:
# trace1 digunakan untuk menampilkan plot dari fft
trace1 = go.Scatter(
    x = time_vec,
    y = filterred_sig,
    mode = 'lines',
    name = 'Ax'
)

trace_ringan = go.Scatter(
    mode='markers',
    x=df_ringan.index,
    y=df_ringan['type'].values,
    name='Ringan',
    marker=dict(
        color='lightBlue',
        size=10,
        line=dict(
            color='black',
            width=2
        )
    ),
)
trace_sedang = go.Scatter(
    mode='markers',
    x=df_sedang.index,
    y=df_sedang['type'].values,
    name='Sedang',
    marker=dict(
        color='orange',
        size=10,
        line=dict(
            color='black',
            width=2
        )
    ),
)
trace_berat = go.Scatter(
    mode='markers',
    x=df_berat.index,
    y=df_berat['type'].values,
    name='Berat',
    marker=dict(
        color='yellow',
        size=10,
        line=dict(
            color='black',
            width=2
        )
    ),
)
layout = go.Layout(
    title="Plot Timeseries ",
    xaxis={'title': "Time (ms)"},
    yaxis={'title': "Amplitude"}
)
fig = go.Figure(data=[trace1, trace_ringan, trace_sedang,
                trace_berat], layout=layout)
fig.show()